<a href="https://colab.research.google.com/github/andryll/Cortisol-Estimator-with-DL/blob/main/notebooks/CortIncepTime.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%%capture
pip install aeon

## Carregando o repositório do GitHub com os dados

In [2]:
!git clone https://github.com/andryll/Cortisol-Estimator-with-DL

Cloning into 'Cortisol-Estimator-with-DL'...
remote: Enumerating objects: 41, done.
remote: Counting objects: 100% (41/41), done.
remote: Compressing objects: 100% (38/38), done.
remote: Total 41 (delta 11), reused 0 (delta 0), pack-reused 0 (from 0)
Receiving objects: 100% (41/41), 2.15 MiB | 4.24 MiB/s, done.
Resolving deltas: 100% (11/11), done.


In [3]:
import tensorflow as tf

gpus = tf.config.list_physical_devices('GPU')
if gpus:
    print(f"GPU(s) detected: {gpus}")
    tf.config.experimental.set_memory_growth(gpus[0], True)
else:
    print("No GPU detected. Please ensure your Colab runtime is set to 'GPU' (Runtime -> Change runtime type -> T4 GPU).")

GPU(s) detected: [PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


## Carregando e Preparando os Dados


1.   Os dados de treino, teste e validação são carregados e concatenados, de modo a desfazer a divisão feita anteriormente.

2.   Em seguida, os dados de teste são normalizados com o MinMaxScaler



In [4]:
import numpy as np
from sklearn.preprocessing import MinMaxScaler

data_X = np.load("/content/Cortisol-Estimator-with-DL/data/X_train.npy")
data_X = np.concatenate((data_X, np.load("/content/Cortisol-Estimator-with-DL/data/X_val.npy")), axis=0)
data_X = np.concatenate((data_X, np.load("/content/Cortisol-Estimator-with-DL/data/X_test.npy")), axis=0)
print("data_X shape:", data_X.shape)

data_y = np.load("/content/Cortisol-Estimator-with-DL/data/y_train.npy")
data_y = np.concatenate((data_y, np.load("/content/Cortisol-Estimator-with-DL/data/y_val.npy")), axis=0)
data_y = np.concatenate((data_y, np.load("/content/Cortisol-Estimator-with-DL/data/y_test.npy")), axis=0)

scaler = MinMaxScaler()
data_y = scaler.fit_transform(data_y.reshape(-1, 1)).flatten()

print("data_y shape:", data_y.shape)

data_X shape: (148, 587, 4)
data_y shape: (148,)


## Realizando a Regressão com o InceptionTime

In [ ]:
from aeon.regression.deep_learning import InceptionTimeRegressor
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
import numpy as np
from tensorflow.keras.callbacks import EarlyStopping # Importar EarlyStopping

# Realizando o KFold split com 10 folds
n_splits = 10
kf = KFold(n_splits=n_splits, shuffle=True, random_state=42)

mses = [] # Lista para armazenar o MSE de cada Fold

print(f"Realizando o {n_splits}-fold cross-validation...")

# Definir o callback de Early Stopping
early_stopping_callback = EarlyStopping(
    monitor='loss',  # Monitorar a perda de validação
    patience=20,         # Número de épocas sem melhora após o qual o treinamento será interrompido
    restore_best_weights=True # Restaura os pesos do modelo da melhor época
)

# Loop iterando cada uma das pastas
for fold, (train_index, test_index) in enumerate(kf.split(data_X)): # Enumerando as pastas
    print(f"\nFold {fold+1}/{n_splits}")

    # Dividindo os dados de acordo com a pasta atual
    X_train_fold, X_test_fold = data_X[train_index], data_X[test_index]
    y_train_fold, y_test_fold = data_y[train_index], data_y[test_index]

    # Inicializando o InceptionTimeRegressor com 100 épocas
    reg = InceptionTimeRegressor(n_epochs=100,
                                 batch_size=8,
                                 verbose = True,
                                 callbacks=[early_stopping_callback])
    # Treinando o Regressor, passando o callback e definindo uma parte para validação
    reg.fit(X_train_fold, y_train_fold)

    # Realizando as predições
    y_pred_fold = reg.predict(X_test_fold)

    # Calculando o MSE para a pasta atual
    mse_fold = mean_squared_error(y_test_fold, y_pred_fold)
    mses.append(mse_fold)
    print(f"MSE para a pasta {fold+1}: {mse_fold}")

# Calculando a média dos MSE
average_mse = np.mean(mses)
print(f"\nAverage MSE across {n_splits} folds: {average_mse}")

Realizando o 10-fold cross-validation...

Fold 1/10


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 4, 587)    │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d (Conv1D)     │ (None, 4, 32)     │     18,784 │ input_layer[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling1d       │ (None, 4, 587)    │          0 │ input_layer[0][0] │
│ (MaxPooling1D)      │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1 (Conv1D)   │ (None, 4, 32)     │     40,960 │ conv1d[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_2 (Conv1D)   │ (None, 4, 32)     │     20,480 │ conv1d[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_3 (Conv1D)   │ (None, 4, 32)     │     10,240 │ conv1d[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_4 (Conv1D)   │ (None, 4, 32)     │     18,784 │ max_pooling1d[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, 4, 128)    │          0 │ conv1d_1[0][0],   │
│ (Concatenate)       │                   │            │ conv1d_2[0][0],   │
│                     │                   │            │ conv1d_3[0][0],   │
│                     │                   │            │ conv1d_4[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalization │ (None, 4, 128)    │        512 │ concatenate[0][0] │
│ (BatchNormalizatio… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation          │ (None, 4, 128)    │          0 │ batch_normalizat… │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_5 (Conv1D)   │ (None, 4, 32)     │      4,096 │ activation[0][0]  │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling1d_1     │ (None, 4, 128)    │          0 │ activation[0][0]  │
│ (MaxPooling1D)      │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_6 (Conv1D)   │ (None, 4, 32)     │     40,960 │ conv1d_5[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_7 (Conv1D)   │ (None, 4, 32)     │     20,480 │ conv1d_5[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_8 (Conv1D)   │ (None, 4, 32)     │     10,240 │ conv1d_5[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_9 (Conv1D)   │ (None, 4, 32)     │      4,096 │ max_pooling1d_1[… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_1       │ (None, 4, 128)    │          0 │ conv1d_6[0][0],   │
│ (Concatenate)       │                   │            │ conv1d_7[0][0],   │
│                     │                   │            │ conv1d_8[0][0],   │
│                     │                   │            │ conv1d_9[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 4, 128)    │        512 │ concatenate_1[0]… │
│ (BatchNormalizatio… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_1        │ (None, 4, 128)    │          0 │ batch_normalizat

 Total params: 604,353 (2.31 MB)

 Trainable params: 602,305 (2.30 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_48      │ (None, 4, 587)    │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1536         │ (None, 4, 32)     │     18,784 │ input_layer_48[0… │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling1d_288   │ (None, 4, 587)    │          0 │ input_layer_48[0… │
│ (MaxPooling1D)      │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1537         │ (None, 4, 32)     │     40,960 │ conv1d_1536[0][0] │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1538         │ (None, 4, 32)     │     20,480 │ conv1d_1536[0][0] │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1539         │ (None, 4, 32)     │     10,240 │ conv1d_1536[0][0] │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1540         │ (None, 4, 32)     │     18,784 │ max_pooling1d_28… │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_288     │ (None, 4, 128)    │          0 │ conv1d_1537[0][0… │
│ (Concatenate)       │                   │            │ conv1d_1538[0][0… │
│                     │                   │            │ conv1d_1539[0][0… │
│                     │                   │            │ conv1d_1540[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 4, 128)    │        512 │ concatenate_288[… │
│ (BatchNormalizatio… │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_384      │ (None, 4, 128)    │          0 │ batch_normalizat… │
│ (Activation)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1541         │ (None, 4, 32)     │      4,096 │ activation_384[0… │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling1d_289   │ (None, 4, 128)    │          0 │ activation_384[0… │
│ (MaxPooling1D)      │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1542         │ (None, 4, 32)     │     40,960 │ conv1d_1541[0][0] │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1543         │ (None, 4, 32)     │     20,480 │ conv1d_1541[0][0] │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1544         │ (None, 4, 32)     │     10,240 │ conv1d_1541[0][0] │
│ (Conv1D)            │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1d_1545         │ (None, 4, 32)     │      4,096 │ max_pooling1d_28… │
│ (Conv1D)            │                   │            │                 

 Total params: 604,353 (2.31 MB)

 Trainable params: 602,305 (2.30 MB)

 Non-trainable params: 2,048 (8.00 KB)

Epoch 1/100
